In [2]:
import pandas as pd
import numpy as np
import bokeh as bk
import copy

import urllib


from bokeh.charts import Bar, Scatter, Line, output_file, show, HeatMap, Histogram
from bokeh.charts.attributes import ColorAttr, CatAttr
from bokeh.plotting  import figure, output_notebook
from bokeh.models import (HoverTool, 
                          ColumnDataSource, 
                          LinearColorMapper, 
                          CustomJS,
                          ColorBar)
                          
from bokeh.palettes import Viridis6, Viridis256, Category10, Plasma
from bokeh.models.widgets import Slider
from bokeh.layouts import column, row
output_notebook(hide_banner=True)

import map_helper as mh


import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = 60


### Helper functions for Barplots

In [3]:
## Helper Functions

TOOLS = "pan,wheel_zoom,box_zoom,reset"

def horiz_cat_barplot(dfm,keys=['Savings','Utility'],extra_key = None,
                      title='',xrange=[0,100],invert_yrange=False,color='red',axis_location="left",
                      height=500,width=500):
    factors = list(dfm[keys[1]])
    xval = dfm[keys[0]]
    
    yrange = factors
    if invert_yrange:
        yrange = factors[::-1]
    
    fig = figure(title=title, tools="", toolbar_location=None,
                y_range=yrange, x_range=xrange,y_axis_location=axis_location,height=height,width=width)

    fig.rect(xval/2, factors, width=xval, height=0.7, color=color,alpha=0.7)
    
    if extra_key:
        x = dfm[extra_key]
        fig.circle(x, factors, size=2, fill_color="orange", line_width=3, alpha=0.5)
    fig.xaxis.major_label_text_font_size = '10pt'
    fig.yaxis.major_label_text_font_size = '10pt'
    fig.yaxis.major_label_text_font_size = '10pt'
    fig.xaxis.axis_label = keys[0]
    return fig

def best_worst_barplot(dfm,keys=['Savings','Utility'],extra_key = None,numrecords=20,
                      title='',xrange=[0,30],invert_yrange=False,color='red',axis_location="left"):
    
    comp_df_sorted = dfm.dropna(subset=[keys[0]]).sort_values(by=keys[0],ascending=True)
    worst_dfm = comp_df_sorted.head(numrecords)
    fig1 = horiz_cat_barplot(worst_dfm,keys=keys,
                             extra_key = None,title='Worst {}'.format(keys[0]),xrange=[-xrange[1],-xrange[0]],
                             invert_yrange=True)

    best_dfm = comp_df_sorted.tail(numrecords)
    fig2 = horiz_cat_barplot(best_dfm,keys=keys,
                             extra_key = None,title='Best {}'.format(keys[0]),color='green',
                             axis_location="right",xrange=xrange)
    return row(fig1,fig2)

### Helper Functions for maps

In [4]:
def process_stats_by_counties(dfm,key='GPCD',groupkey='Year',aggfunc='mean',srcpath=''):
    
    # Initialize dataframe of regions and counties
    
    region_counties_df = pd.read_csv(srcpath)
    region_counties_df = region_counties_df[['Hydrologic Region','County']]

    list_df = []
    for elt in dfm[groupkey].unique():
        temp_df = copy.deepcopy(region_counties_df)
        temp_df[groupkey] = elt
        list_df.append(temp_df)

    # Overwrite initial dataframe
    region_counties_df = pd.concat(list_df)

    grouped_df = dfm.groupby(['Hydrologic Region','County',groupkey])[[key]].agg(aggfunc).reset_index()

    # Adding missing groups if present
    grouped_df = grouped_df.merge(region_counties_df,on=['Hydrologic Region','County',groupkey],how='outer')

    # If counties are missing in some groups fill In Average of hydrologic region
    grouped_df[key] = grouped_df.groupby(['Hydrologic Region',groupkey]).transform(lambda x: x.fillna(x.mean()))
    return grouped_df.groupby(['County',groupkey])[key].agg(aggfunc).reset_index()
    

def add_location_to_dfm(dfm,state="ca"):
    """ Given dataframe with County field adds county boundaries in order to 
    be used in the plotting routine  """
    # Build County boundary DataFrame from bokeh county data
    from bokeh.sampledata.us_counties import data as counties
    counties = {
                code: county for code, county in counties.items() if county["state"] == state
               }
    county_xs = [county["lons"] for county in counties.values()]
    county_ys = [county["lats"] for county in counties.values()]
    county_names = [county['name'] for county in counties.values()]
    
    location_df = pd.DataFrame({'County':county_names,'x':county_xs,'y':county_ys})
    return dfm.merge(location_df,on='County',how='left')


def interactive_county_map(dfm,key='GPCD',slider_key='Year',initial_query='Year == 2014',
                    title='California GPCD',tools = "pan,wheel_zoom,box_zoom,reset,hover,save", 
                    width=600,height=600,zscale='linear'):
    """ Plots interactive map given dataframe with COunty boundary fields as wall as 
    key value and slider_key present in columns"""
    palette = Viridis256
    palette = palette[::-1]

    if zscale == 'log':
        color_mapper = LogColorMapper(palette=palette,low=dfm[key].min(),high=dfm[key].max())
    else:
        color_mapper = LinearColorMapper(palette=palette,low=dfm[key].min(),high=dfm[key].max())

    source = ColumnDataSource(dfm.dropna(), id='src')
    source_flt = ColumnDataSource(dfm.query(initial_query).fillna(-1), id='src_flt')

    p = figure(title=title, tools=tools,x_axis_location=None, y_axis_location=None,
               width = width, height=height)
    p.grid.grid_line_color = None

    p.patches('x', 'y', source=source_flt,
              fill_color={'field': key, 'transform': color_mapper},
              fill_alpha=0.7, line_color="white", line_width=0.5)

    hover = p.select_one(HoverTool)
    hover.point_policy = "follow_mouse"
    hover.tooltips = [
        ("County", "@County"),
        ("{}".format(key), "@{}".format(key)),
        ]



    callback_js_code="""
                     var orig_data = s1.data;
                     var filtered_data = s2.data;
                     var selected = cb_obj["value"];

                     for (var key in orig_data) {{
                         filtered_data[key] = [];
                         for (var i = 0; i < orig_data['County'].length; ++i) {{
                             if (orig_data['{VARNAME}'][i] === selected)  {{
                                 filtered_data[key].push(orig_data[key][i]);
                             }}
                          }}
                     }}
                     s2.trigger("change");
                     """.format(VARNAME = slider_key)

    callback = CustomJS(args=dict(s1=source,s2=source_flt), code=callback_js_code)


    slider = Slider(start=dfm[slider_key].min(), 
                    end=dfm[slider_key].max(), 
                    value=dfm[slider_key].min(), step=1, 
                    title="Select {}".format(slider_key), width=width,
                    callback=callback)


    color_bar = ColorBar(color_mapper=color_mapper, location=(0, 0), orientation='vertical')
    p.add_layout(color_bar, 'right')
    p.toolbar_location = 'left'
    return column(slider,p)


## Re-Process Dataset

In [8]:
# Dataset locations

#Pre_processed_dset_pth = 'https://s3-us-west-1.amazonaws.com/tdidataset/TDI/Pre_processed_WU_dataset.csv'
#DFT_PTH = 'https://s3-us-west-1.amazonaws.com/tdidataset/TDI/hydrologic_regions_vs_counties.csv'
#County_bounday_pth = 'https://s3-us-west-1.amazonaws.com/tdidataset/TDI/counties_boundaries.hdf'

Pre_processed_dset_pth = './Pre_processed_WU_dataset.csv'
DFT_PTH = './hydrologic_regions_vs_counties.csv'
County_bounday_pth = './counties_boundaries.hdf'



In [9]:
print('Downloading preprocessed dataset from:',Pre_processed_dset_pth)
df = pd.read_csv(Pre_processed_dset_pth)
print('Downloading county boundary data from:',County_bounday_pth)
#urllib.request.urlretrieve(County_bounday_pth,'counties_boundaries.hdf')
location_df = pd.read_hdf('./counties_boundaries.hdf')
#df.head(2)

### Parse datetime

In [34]:

df['Date'] = pd.to_datetime(df.Date)
df['Date'] = df.Date.apply(lambda x: x.date())
#df['Date'] = df.Date.apply(lambda x:x.strftime("%Y-%m"))
df['Year']=df.Date.apply(lambda x: x.year)
df['Month']=df.Date.apply(lambda x: x.strftime('%b'))
df['monthcode']=df.Date.apply(lambda x: x.month)
df['Conservation target'] = df['Conservation target']*100

df['Prod_res'] = df['Production']*df['% Residential']*0.01
df['Prod_ind_ag'] = df['Production']-df['Prod_res']

df

Hydrologic Region                                     Utility  \
0      San Francisco Bay       East Bay Municipal Utilities District   
1      San Francisco Bay       East Bay Municipal Utilities District   
2      San Francisco Bay       East Bay Municipal Utilities District   
3      San Francisco Bay       East Bay Municipal Utilities District   
4      San Francisco Bay       East Bay Municipal Utilities District   
5      San Francisco Bay       East Bay Municipal Utilities District   
6      San Francisco Bay       East Bay Municipal Utilities District   
7      San Francisco Bay       East Bay Municipal Utilities District   
8      San Francisco Bay       East Bay Municipal Utilities District   
9      San Francisco Bay       East Bay Municipal Utilities District   
10     San Francisco Bay       East Bay Municipal Utilities District   
11     San Francisco Bay       East Bay Municipal Utilities District   
12     San Francisco Bay       East Bay Municipal Utilities District   
13     San Francisco Bay       East Bay Municipal Utilities District   
14     San Francisco Bay       East Bay Municipal Utilities District   
15     San Francisco Bay       East Bay Municipal Utilities District   
16     San Francisco Bay       East Bay Municipal Utilities District   
17     San Francisco Bay       East Bay Municipal Utilities District   
18     San Francisco Bay       East Bay Municipal Utilities District   
19     San Francisco Bay       East Bay Municipal Utilities District   
20     San Francisco Bay       East Bay Municipal Utilities District   
21     San Francisco Bay       East Bay Municipal Utilities District   
22     San Francisco Bay       East Bay Municipal Utilities District   
23     San Francisco Bay       East Bay Municipal Utilities District   
24     San Francisco Bay       East Bay Municipal Utilities District   
25     San Francisco Bay       East Bay Municipal Utilities District   
26     San Francisco Bay       East Bay Municipal Utilities District   
27     San Francisco Bay       East Bay Municipal Utilities District   
28     San Francisco Bay       East Bay Municipal Utilities District   
29     San Francisco Bay       East Bay Municipal Utilities District   
...                  ...                                         ...   
12953  San Joaquin River  Mountain House Community Services District   
12954  San Joaquin River  Mountain House Community Services District   
12955  San Joaquin River  Mountain House Community Services District   
12956  San Joaquin River  Mountain House Community Services District   
12957  San Joaquin River  Mountain House Community Services District   
12958  San Joaquin River  Mountain House Community Services District   
12959  San Joaquin River  Mountain House Community Services District   
12960  San Joaquin River  Mountain House Community Services District   
12961  San Joaquin River  Mountain House Community Services District   
12962  San Joaquin River  Mountain House Community Services District   
12963  San Joaquin River  Mountain House Community Services District   
12964  San Joaquin River  Mountain House Community Services District   
12965  San Joaquin River  Mountain House Community Services District   
12966  San Joaquin River  Mountain House Community Services District   
12967  San Joaquin River  Mountain House Community Services District   
12968  San Joaquin River  Mountain House Community Services District   
12969  San Joaquin River  Mountain House Community Services District   
12970  San Joaquin River  Mountain House Community Services District   
12971  San Joaquin River  Mountain House Community Services District   
12972  San Joaquin River  Mountain House Community Services District   
12973  San Joaquin River  Mountain House Community Services District   
12974  San Joaquin River  Mountain House Community Services District   
12975        North Coast                                  Cloverdale   
12976        North Coast                       

#### 2013 production data is in another column: Stack production data in one column


In [31]:

initcols = ['Utility_name','County','Hydrologic Region','Year','Month','% Residential']
subdf_1 = df[initcols+['Production' ]]
subdf_2 = df[initcols+['Production 2013' ]]
subdf_2.rename(columns = {'Production 2013':'Production'},inplace=True)
subdf_2['Year'] = 2013
subdf = pd.concat([subdf_1,subdf_2])
subdf['Date'] = subdf.Year.astype('str')+'-'+subdf.Month
subdf['datetime'] = pd.to_datetime(subdf['Date'])
subdf['Date'] = subdf.datetime.apply(lambda x:x.strftime("%Y-%m"))
subdf['Prod_res'] = subdf['Production']*subdf['% Residential']*0.01
subdf['Prod_ind_ag'] = subdf['Production']-subdf['Prod_res']

### Production over time

In [44]:
f = subdf.groupby(['Hydrologic Region','Date']).agg('mean').reset_index()
src = ColumnDataSource(f)
tools=[HoverTool()]

key = 'Prod_res'

p1 = Bar(src.data,'Date', values=key, title="Total Residential Production vs Date by Region",agg='sum', 
        stack = 'Hydrologic Region', width=700, height=700, palette = Viridis6,tools=TOOLS)
p1.legend.location = 'top_right'
p1.legend.background_fill_alpha = 0.7

avg_gp = process_stats_by_counties(df,key=key,groupkey='monthcode',aggfunc='mean',srcpath=DFT_PTH)

location_df.query('State == "CA"',inplace=True)
data2 = avg_gp.merge(location_df,on='County',how='left')

cal_fig = interactive_county_map(data2,key=key,slider_key='monthcode',initial_query='monthcode == 1',
                             title='California Residential Water Usage per Month by County',
                             tools = "pan,wheel_zoom,box_zoom,reset,hover,save",
                             width=700,height=700)

show(row(p1,cal_fig))

In [43]:
f = subdf.groupby(['Hydrologic Region','Date']).agg('mean').reset_index()
src = ColumnDataSource(f)
tools=[HoverTool()]

key = 'Prod_ind_ag'

p1 = Bar(src.data,'Date', values=key, title="Total Agricultural/Industrial usage vs Date by Region",agg='sum', 
        stack = 'Hydrologic Region', width=700, height=700, palette = Viridis6,tools=TOOLS)
p1.legend.location = 'top_right'
p1.legend.background_fill_alpha = 0.7

avg_gp = process_stats_by_counties(df,key=key,groupkey='monthcode',aggfunc='mean',srcpath=DFT_PTH)

location_df.query('State == "CA"',inplace=True)
data2 = avg_gp.merge(location_df,on='County',how='left')

cal_fig = interactive_county_map(data2,key=key,slider_key='monthcode',initial_query='monthcode == 1',
                             title='California Agricultural/Industrial Water Usage per Month by County',
                             tools = "pan,wheel_zoom,box_zoom,reset,hover,save",
                             width=700,height=700)

show(row(p1,cal_fig))

#### Cumulative savings per Utility

In [45]:

prod_df = subdf.groupby(['Hydrologic Region', 'County','Utility_name','Year']).agg(sum).reset_index()
# Year 2014 and 2017 data is incomplete let's drop them
prod_df.query('Year != 2014 & Year != 2017',inplace=True)
#let's calculate savings from 2013 to 2016
lst_dfm = []
for yr, gp in prod_df.groupby('Year'):
    gp.rename(columns={'Production':'Tot_Production_{}'.format(yr)},inplace=True)
    gp.drop('Year',axis=1,inplace=True)
    lst_dfm.append(gp)

    
comp_df = pd.merge(lst_dfm[0],lst_dfm[1],on=['Hydrologic Region', 'County','Utility_name'],how='outer')
comp_df = pd.merge(comp_df,lst_dfm[2],on=['Hydrologic Region', 'County','Utility_name'],how='outer')

In [46]:
comp_df['Savings 2015-2016'] = (comp_df.Tot_Production_2015-comp_df.Tot_Production_2016)/comp_df.Tot_Production_2015*100
comp_df['Savings 2013-2016'] = (comp_df.Tot_Production_2013-comp_df.Tot_Production_2016)/comp_df.Tot_Production_2013*100
comp_df = comp_df.dropna()
#comp_df.head()

In [47]:
fig = best_worst_barplot(comp_df,keys=['Savings 2015-2016','Utility_name'],extra_key = None,numrecords=20,
                      title='',xrange=[0,80],invert_yrange=False,color='red',axis_location="left")
show(fig)